In [1]:
pip install sklearn

Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install keras.utils 

Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install tensorflow

Note: you may need to restart the kernel to use updated packages.


In [4]:
pip install opencv-python

In [5]:
import numpy as np
import pandas as pd
import os
for dirname, _, filenames in os.walk('D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\AbdomenCT\000000.jpeg
D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\AbdomenCT\000001.jpeg
D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\AbdomenCT\000002.jpeg
D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\AbdomenCT\000003.jpeg
D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\AbdomenCT\000004.jpeg
D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\AbdomenCT\000005.jpeg
D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\AbdomenCT\000006.jpeg
D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\AbdomenCT\000007.jpeg
D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\AbdomenCT\000008.jpeg
D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT D

In [17]:
import numpy as np
import pandas as pd
from tensorflow.keras.utils import to_categorical
import matplotlib.pyplot as plt
import tensorflow as tf
from tensorflow.keras.preprocessing.image import ImageDataGenerator
import os
from tqdm import tqdm
from random import shuffle  
from zipfile import ZipFile
from PIL import Image
import cv2
from tensorflow.keras import models
from tensorflow.keras import layers
from tensorflow.keras import activations
from tensorflow.keras import Model
from tensorflow.keras import callbacks

%matplotlib inline

In [ ]:
classes = {'AbdomenCT': 0, 'BreastMRI': 1, 'ChestCT': 2, 'CXR': 3, 'Hand': 4, 'HeadCT': 5}

In [ ]:
ImageWidth=64
ImageHeight=64
ImageSize=(ImageWidth, ImageHeight)
BatchSize=64
NoOfClass = 6
EPOCHS = 5

In [ ]:
AbdomenDir='D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\AbdomenCT'
BreastMRIDir='D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\BreastMRI'
ChestCTDir='D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\ChestCT'
CXRDir='D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\CXR'
HandDir='D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\Hand'
HeadCTDir='D:\MSC COMPUTER SCIENCE\Term 2 AIMV\Project\datasets\FINAL AIMV PROJECT DATASETS\HeadCT'

In [ ]:
def assign_label(image,class_type):
    return class_type
X = []
y = []
def make_train_data(class_type,Dir):
    for image in tqdm(os.listdir(Dir)):
        label=assign_label(image,class_type)
        path=os.path.join(Dir,image)
        image=cv2.imread(path,cv2.IMREAD_COLOR)
        image=cv2.resize(image, (ImageWidth, ImageHeight))
        
        X.append(np.array(image))
        y.append(str(label))

In [ ]:
make_train_data(classes.get('AbdomenCT'), AbdomenDir)
make_train_data(classes.get('BreastMRI'), BreastMRIDir)
make_train_data(classes.get('ChestCT'), ChestCTDir)
make_train_data(classes.get('CXR'), CXRDir)
make_train_data(classes.get('Hand'), HandDir)
make_train_data(classes.get('HeadCT'), HeadCTDir)

In [ ]:
len(X)
y=np.array(y)
X=np.array(X)
X.shape
X.shape, y.shape

In [ ]:
from sklearn.model_selection import train_test_split
X_train,X_test, y_train, y_test=train_test_split(X, y, shuffle=True, test_size=0.5, random_state=58954)

In [ ]:
N=len(set(y_train))
print("Number of classes, ", N)

In [ ]:
X_train=X_train.astype('float32')/255
X_test=X_test.astype('float32')/255

In [ ]:
y_train=to_categorical(y_train, num_classes=6)
y_test=to_categorical(y_test, num_classes=6)

In [ ]:
labels = '''AbdomenCT
BreastMRI
ChestCT
CXR
Hand
HeadCT'''.split("\n")
plt.figure(figsize=(10,10))
j = 1
for i in np.random.randint(0,1000,16):
    plt.subplot(4,4,j); j+=1
    plt.imshow(X_train[i],cmap = 'Greys')
    plt.axis('off')
    plt.title("Actual: {}".format(labels[np.argmax(y_train[i])]))

In [ ]:
i= layers.Input(shape = (X_train[0].shape))
x=layers.Conv2D(64, (5,5), activation='relu', strides = (4,4), padding= 'same')(i)
x=layers.Conv2D(32, (5,5), activation='relu', strides = (4,4), padding= 'same')(x)
x=layers.Conv2D(32, (5,5), activation='relu', strides = (4,4), padding= 'same')(x)
x=layers.Flatten()(x)
x=layers.Dense(256, activation='relu')(x)
x=layers.Dropout(0.8)(x)
x=layers.Dense(128, activation='relu')(x)
x=layers.Dropout(0.8)(x)
x=layers.Dense(N, activation='softmax')(x)

model = Model(i, x)

In [ ]:
model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate=0.01), loss='categorical_crossentropy', metrics=['accuracy'])
reducelr=callbacks.ReduceLROnPlateau(monitor='val_accuracy', factor=0.1,
                              patience=3, min_lr=0.01)
frame=model.fit(X_train, y_train, epochs = EPOCHS, batch_size = BatchSize, validation_data=  (X_test,y_test), callbacks=[reducelr])

In [ ]:
import matplotlib.pyplot as plt
trainacc=frame.history['accuracy']
valacc=frame.history['val_accuracy']
epochs = range(1,6)
plt.plot(epochs, trainacc, 'g', label='Training accuracy')
plt.plot(epochs, valacc, 'b', label='validation accuracy')
plt.title('Training and Validation accuracy')
plt.xlabel('Epochs')
plt.ylabel('Accuracy')
plt.legend()
plt.show()

In [ ]:
from sklearn.metrics import confusion_matrix
import itertools
def plot_confusion_matrix(cm, classes,
                          normalize=False,
                          title='Confusion matrix',
                          cmap=plt.cm.Blues):
    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
        print("Normalized confusion matrix")
    else:
        print('Confusion matrix, without normalization')
    print(cm)

In [ ]:
p_test = model.predict(X_test).argmax(axis=1)
cm = confusion_matrix(np.argmax(y_test, axis= 1), p_test)
plot_confusion_matrix(cm, list(range(5)))